#  Highly Performant TensorFlow Batch Inference on Image Data Using the SageMaker Python SDK 

이 노트북에서는 SageMaker Batch Transform을 사용하여 대규모 데이터 세트에 대한 추론을 얻는 방법을 보여줍니다. 이를 위해 TensorFlow Serving 모델을 사용하여 대규모 이미지 데이터 세트에서 배치 추론을 실행할 것입니다. TensorFlow Serving 컨테이너의 새로운 전처리 및 후처리 기능을 SageMaker 기반으로 실행하여 TensorFlow 모델이 S3에 저장된 데이터를 이용하여 바로 추론을 실행하고 후처리된 결과를 다시 S3에 저장합니다.

데이터 세트는 [Open Images V5 Dataset](https://storage.googleapis.com/openimages/web/index.html)의 서브셋인 [“Challenge 2018/2019"](https://github.com/cvdfoundation/open-images-dataset#download-the-open-images-challenge-28182019-test-set) 을 사용합니다. 이 데이터셋은 .jpg 형식의 100,000개 이미지로 총 10GB로 구성됩니다. 데모를 위해 사용할 모델은 [model](https://github.com/tensorflow/models/tree/master/official/resnet#pre-trained-model)를 이용합니다. 이 모델은 이미지 분류 모델이며, ResNet-50를 기반으로 이미지넷 데이터를 이용하여 학습되었으며 Tensorflow SavedModel형식으로 저장되었습니다. 

이 모델을 사용하여 각 이미지가 속한 클래스를 예측합니다. TensorFlow SavedModel과 함께 사용될 전처리, 후처리 스크립트를 작성하고 패키징한 후, GPU 가속 인스턴스에서 SageMaker 일괄 변환을 사용하여 대규모 데이터 세트에 대한 추론을 빠르고 효율적이며 대규모로 얻는 방법을 보여줍니다.

## Setup 

필요한 라이브러리들을 가져오고, 작업을 실행할 Amazon SageMaker 세션을 선언하고, 접근제어가 설정된 IAM 권한(Role)을 가져옵니다. 

In [1]:
import numpy as np
import os
import sagemaker
from sagemaker import get_execution_role

sagemaker_session = sagemaker.Session()
role = get_execution_role()

region = sagemaker_session.boto_region_name
bucket = sagemaker_session.default_bucket()
prefix = "sagemaker/DEMO-tf-batch-inference-jpeg-images-python-sdk"
print("Region: {}".format(region))
print("S3 URI: s3://{}/{}".format(bucket, prefix))
print("Role:   {}".format(role))

Region: ap-northeast-1
S3 URI: s3://sagemaker-ap-northeast-1-308961792850/sagemaker/DEMO-tf-batch-inference-jpeg-images-python-sdk
Role:   arn:aws:iam::308961792850:role/service-role/AmazonSageMaker-ExecutionRole-20200220T105738


## Inspecting the SavedModel

추론을 위해, S3에 저장된 추론용 이미지 데이터를 TensorFlow SavedModel(https://www.tensorflow.org/guide/saved_model)의 서빙용 서명(serving signature)과 일치하도록 전처리해야 합니다. Tensorflow에서 제공하는 saved_model_cli (https://github.com/tensorflow/tensorflow/blob/master/tensorflow/python/tools/saved_model_cli.py)를 이용하여 SignatureDef를 살펴봅니다. 다음은 ResNet-50 v2 (NCHW, JPEG) (https://github.com/tensorflow/models/tree/master/official/resnet#pre-trained-model)의 서빙용 서명입니다.



In [2]:
!aws s3 cp s3://sagemaker-sample-data-{region}/batch-transform/open-images/model/resnet_v2_fp32_savedmodel_NCHW_jpg.tar.gz .
!tar -zxf resnet_v2_fp32_savedmodel_NCHW_jpg.tar.gz
!saved_model_cli show --dir resnet_v2_fp32_savedmodel_NCHW_jpg/1538687370/ --all

download: s3://sagemaker-sample-data-ap-northeast-1/batch-transform/open-images/model/resnet_v2_fp32_savedmodel_NCHW_jpg.tar.gz to ./resnet_v2_fp32_savedmodel_NCHW_jpg.tar.gz
2021-07-13 15:14:28.749301: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /usr/local/cuda-10.0/lib64:/usr/local/cuda-10.0/extras/CUPTI/lib64:/usr/local/cuda-10.0/lib:/usr/local/cuda-10.0/efa/lib:/opt/amazon/efa/lib:/opt/amazon/efa/lib64:/usr/local/cuda/lib:/usr/local/cuda/lib64:/usr/local/cuda/extras/CUPTI/lib64:/opt/amazon/efa/lib64:/opt/amazon/openmpi/lib64:/usr/local/lib:/usr/lib:/lib:/usr/local/cuda/lib:/usr/local/cuda/lib64:/usr/local/cuda/extras/CUPTI/lib64:/opt/amazon/efa/lib64:/opt/amazon/openmpi/lib64:/usr/local/lib:/usr/lib:/lib::/home/ec2-user/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/tensorflow
2021-07-13 15:14:28.7

SageMaker TensorFlow Serving Container는 모델을 Tensorflow SavedModel로 저장할 때 선언되는 serve_default 라는 SignatureDef를 사용합니다. 이 SignatureDef는 모델이 임의의 길이의 문자열을 입력으로 받아들이고, 정수형의 분류 클래스와 실수형의 확률을 리턴한다고 되어있습니다. 이 분류모델을 사용할 때 JPEG 이미지를 나타내는 입력 문자열은 base-64 인코딩된 형식을 사용하며 SaveModel이 이를 디코드할 것입니다. 



## Writing a pre- and post-processing script

We will package up our SavedModel with a Python script named `inference.py`, which will pre-process input data going from S3 to our TensorFlow Serving model, and post-process output data before it is saved back to S3:

In [3]:
!pygmentize code/inference.py

# Copyright 2019 Amazon.com, Inc. or its affiliates. All Rights Reserved.
#
# Licensed under the Apache License, Version 2.0 (the "License"). You
# may not use this file except in compliance with the License. A copy of
# the License is located at
#
#     http://aws.amazon.com/apache2.0/
#
# or in the "license" file accompanying this file. This file is
# distributed on an "AS IS" BASIS, WITHOUT WARRANTIES OR CONDITIONS OF
# ANY KIND, either express or implied. See the License for the specific
# language governing permissions and limitations under the License.

import base64
import io
import json

import requests


def input_handler(data, context):
    """Pre-process request input before it is sent to TensorFlow Serving REST API

    Args:
        data (obj): the request data stream
        context (Context): an object containing request and configuration details

    Returns:
        (dict): a JSON-serializable dict that contains request body and headers
    """

    if context.request_

input_handler는 추론 요청을 가로챈 후, 요청 본문을 base-64로 인코딩하고, TensorFlow Serving의 REST API(https://www.tensorflow.org/tfx/serving/api_rest )에 맞도록 하도록 요청 본문의 형식을 조정합니다. input_handler 함수의 반환 값은 TensorFlow Serving 요청에서 요청 본문으로 사용됩니다.

TFS REST API(https://www.tensorflow.org/tfx/serving/api_rest#encoding_binary_values )에 따라 바이너리 데이터는 반드시 "b64"라는 키를 사용해야 합니다. 서빙 서명의 입력 텐서에 접미사 "_bytes"가 있고, "b64" 키 아래의 인코딩된 이미지 데이터는 이 "image_bytes" 텐서로 전달될 것입니다. 일부 서빙 서명은 base-64로 인코딩된 문자열 대신 부동 소수점 또는 정수형의 텐서를 사용할 수 있습니다. 하지만 (이미지와 같은) 바이너리 데이터의 경우 JSON타입으로 바이너리를 나타낼때는 크기가 너무 커질 수 있으므로 base-64 문자열이 보다 추천됩니다. 



추론을 위한 각 요청의 request body에는 직렬화된 JPEG 이미지가 포함될 것이고, input_handler를 통과한 후 TensorFlow Serving이 받아들이는 request body는 다음과 같은 형식이 될 것입니다. 

`{"instances": [{"b64":"[base-64 encoded JPEG image]"}]}`

`output_handler` 반환 값의 첫 번째 필드는 SageMaker Batch Transform이 예측결과로 S3에 저장하는 값입니다. 이 경우 `output_handler`는 수정되지 않은 상태로 콘텐츠를 S3에 전달합니다.

Tensorflow Serving과 전처리 및 후처리 함수를 통해 이미지 뿐 아니라 모든 데이터 형식에서 추론을 실행할 수 있습니다. `input_handler`와 `output_handler`에 대한 보다 자세한 내용은 SageMaker TensorFlow Serving Container README(https://github.com/aws/sagemaker-tensorflow-serving-container/blob/master/README.md )를 참조하십시오.


## Packaging a Model

전처리 및 후처리 스크립트를 작성한 후, 이 스크립트와 TensorFlow SavedModel을 함께 model.tar.gz 파일로 패키징합니다. 이 패키지는 S3에 업로드 되고, 이후 SageMaker TensorFlow Serving Container에서 사용될 것입니다. `inference.py` 스크립트와 SavedModel이 패키징된 `model.tar.gz` 파일의 구조는 다음과 같습니다. 


In [4]:
!tar -cvzf model.tar.gz code --directory=resnet_v2_fp32_savedmodel_NCHW_jpg 1538687370

code/
code/inference.py
1538687370/
1538687370/variables/
1538687370/variables/variables.index
1538687370/variables/variables.data-00000-of-00001
1538687370/saved_model.pb


`1538687370`은 SavedModel의 모델 버전 번호를 나타내며 이 디렉토리에는 SavedModel 아티팩트가 포함됩니다. 코드 디렉토리에는 사전 처리 및 사후 처리 스크립트인 `inference.py`가 포함되어 있습니다. 또한 변환 작업이 시작되기 전에 Python 패키지 색인에서 `pip`를 사용하여 종속성을 설치하기 위해 선택적으로 `requirements.txt` 파일을 포함할 수 있습니다. 이 예제 노트북에서는 의존관계가 필요하지 않으므로 사용하지 않았습니다.

Batch Transform 작업을 실행하는 데 사용할 SageMaker 모델을 만들 때 이 `model.tar.gz`를 사용합니다. 모델 패키징에 대해 자세히 알아보려면 SageMaker TensorFlow Serving Container [README](https://github.com/aws/sagemaker-tensorflow-serving-container/blob/master/README.md)를 참조하세요.

## Run a Batch Transform job

다음으로 데이터 처리 스크립트와 GPU 기반 Amazon SageMaker 모델을 사용하여 Batch Transform 작업을 실행합니다. 우리는 2개의 인스턴스 클러스터에서 추론을 실행할 것이지만 인스턴스 개수를 더 늘리거나 줄일 수 있습니다. S3에 저장된 오브젝트는 인스턴스 전체로 분산될 것입니다. 

아래 코드는 배치 추론에 사용될 SageMaker 모델 엔터티를 생성하고 해당 모델을 사용하여 Batch Transform 작업을 실행합니다. 모델은 TFS 컨테이너에 대한 참조와 TensorFlow SavedModel 및 전처리/후처리용 `inference.py` 스크립트가 내장된 `model.tar.gz`을 포함하고 있습니다. 

In [5]:
import os
import sagemaker
from sagemaker.tensorflow.serving import Model

s3_path = "s3://{}/{}".format(bucket, prefix)

model_data = sagemaker_session.upload_data("model.tar.gz", bucket, os.path.join(prefix, "model"))

tensorflow_serving_model = Model(
    model_data=model_data, role=role, framework_version="1.13", sagemaker_session=sagemaker_session
)

input_path = "s3://sagemaker-sample-data-{}/batch-transform/open-images/jpg".format(region)

print("Model data S3 path: {}".format(model_data))
print("Input S3 path: {}".format(input_path))

The class sagemaker.tensorflow.serving.Model has been renamed in sagemaker>=2.
See: https://sagemaker.readthedocs.io/en/stable/v2.html for details.


Model data S3 path: s3://sagemaker-ap-northeast-1-308961792850/sagemaker/DEMO-tf-batch-inference-jpeg-images-python-sdk/model/model.tar.gz
Input S3 path: s3://sagemaker-sample-data-ap-northeast-1/batch-transform/open-images/jpg


변환 작업을 생성하기 전에 입력 데이터 중 일부를 검사해 보겠습니다. 다음은 데이터세트의 첫 번째 이미지입니다.

<img src="sample_image/00000b4dcff7f799.jpg">

입력 경로의 데이터는 다양한 크기와 모양의 JPEG 이미지 100,000개로 구성됩니다. 다음은 그 서브셋입니다.

In [6]:
!echo "Transform input path: {input_path}"
!aws s3 ls {input_path}/000 --human-readable

Transform input path: s3://sagemaker-sample-data-ap-northeast-1/batch-transform/open-images/jpg
2019-07-26 05:40:04  126.2 KiB 00000b4dcff7f799.jpg
2019-07-26 05:40:04  115.8 KiB 00001a21632de752.jpg
2019-07-26 05:40:08  151.0 KiB 0000d67245642c5f.jpg
2019-07-26 05:40:03  159.9 KiB 0001244aa8ed3099.jpg
2019-07-26 05:40:08  115.0 KiB 000172d1dd1adce0.jpg
2019-07-26 05:40:04   65.4 KiB 0001c8fbfb30d3a6.jpg
2019-07-26 05:40:04   70.4 KiB 0001dd930912683d.jpg
2019-07-26 05:40:04   73.0 KiB 0002c96937fae3b3.jpg
2019-07-26 05:40:04  109.2 KiB 0002f94fe2d2eb9f.jpg
2019-07-26 05:40:04  119.2 KiB 000305ba209270dc.jpg
2019-07-26 05:40:06  119.5 KiB 000313fed9979d24.jpg
2019-07-26 05:40:04   77.2 KiB 0003a523fa9b2a3f.jpg
2019-07-26 05:40:04   84.9 KiB 0003d1c3be9ed3d6.jpg
2019-07-26 05:40:08   82.9 KiB 000455be7b222c04.jpg
2019-07-26 05:40:04  104.8 KiB 0004fdbc5b94c7c2.jpg
2019-07-26 05:40:05  144.0 KiB 0005339c44e6071b.jpg
2019-07-26 05:40:05   75.2 KiB 0005aea8c9144c77.jpg
2019-07-26 05:40:05 

이제 SageMaker 모델을 생성했으므로 이를 사용하여 Batch Transform을 실행하고 일괄로 예측작업을 할 수 있습니다. 입력 S3 데이터, 입력 데이터의 콘텐츠 유형, 출력 S3 데이터, 인스턴스 유형 및 개수를 지정합니다.

성능 향상을 위해 두개의 파라미터를 추가하였습니다. `max_concurrent_transforms`는 한 번에 변환 작업의 각 인스턴스에 보낼 수 있는 최대 병렬 요청 수를, `max_payload` 각 request body의 최대 크기를 제어합니다.

이미지와 같이 줄 바꿈 문자로 분할할 수 없는 전체 S3 객체에 대해 추론을 수행하는 경우 `max_payload`를 데이터 세트에서 가장 큰 S3 객체보다 약간 더 크게 설정하고, `max_concurrent_transforms` 매개변수는 2의 제곱값을 사용하여 처리량을 최대화하는 값을 실험적으로 찾습니다. 예를 들어, 여기서는 몇 번의 실험 후 `max_concurrent_transforms`를 64로 설정하였고, S3 저장된 객체중 가장 큰 객체가 1MB 미만이기 때문에 max_payload를 1로 설정했습니다.

In [ ]:
output_path = os.path.join(s3_path, "output")
tensorflow_serving_transformer = tensorflow_serving_model.transformer(
    instance_count=2,
    instance_type="ml.p3.2xlarge",
    max_concurrent_transforms=64,
    max_payload=1,
    output_path=output_path,
)

print("Transform input S3 path:  {}".format(input_path))
print("Transform output S3 path: {}".format(output_path))
tensorflow_serving_transformer.transform(input_path, content_type="application/x-image")
tensorflow_serving_transformer.wait()

Transform input S3 path:  s3://sagemaker-sample-data-ap-northeast-1/batch-transform/open-images/jpg
Transform output S3 path: s3://sagemaker-ap-northeast-1-308961792850/sagemaker/DEMO-tf-batch-inference-jpeg-images-python-sdk/output
.................................INFO:__main__:starting services
INFO:__main__:using default model name: model
INFO:__main__:tensorflow serving model config: 
model_config_list: {
  config: {
    name: "model",
    base_path: "/opt/ml/model",
    model_platform: "tensorflow"
  },
}


INFO:__main__:nginx config: 
load_module modules/ngx_http_js_module.so;

worker_processes auto;
daemon off;
pid /tmp/nginx.pid;
error_log  /dev/stderr error;

worker_rlimit_nofile 4096;

events {
  worker_connections 2048;
}

http {
  include /etc/nginx/mime.types;
  default_type application/json;
  access_log /dev/stdout combined;
  js_include tensorflow-serving.js;

  upstream tfs_upstream {
    server localhost:10001;
  }

  upstream gunicorn_upstream {
    server unix:/tmp/

변환작업이 끝난 후에는 입력 경로의 각 객체애 대한 출력 경로에서 S3 객체를 찾습니다. 이 객체는 모델의 추론 결과를 포함하며, 입력 객체와 이름이 같지만 `.out`이 추가됩니다.

In [ ]:
!aws s3 ls {output_path}/000 --human-readable

출력 객체 중 하나를 검사하여 TensorFlow Serving 모델의 예측결과를 확인합니다. 다음은 위에 표시된 예제 이미지에서 가져온 결과입니다.

In [ ]:
!aws s3 cp {output_path}/00000b4dcff7f799.jpg.out .
!cat 00000b4dcff7f799.jpg.out

In [ ]:
import json

with open("00000b4dcff7f799.jpg.out", "r") as f:
    jstr = json.load(f)
    print(jstr)

    # Subtracting 1 for "background" class
    class_index = jstr["predictions"][0]["classes"] - 1
    print(type(jstr))
    probabilities = jstr["predictions"][0]["probabilities"]
    print(probabilities)
    import numpy as np

    probs = np.argmax(probabilities)
    print(probs)
    print(probabilities[class_index + 1])

    # Index 864 corresponds to "tow truck"
    print("Class index: {}".format(class_index))

## Conclusion

SageMaker Batch Transform은 대규모 데이터 세트를 빠르고 확장 가능하게 처리할 수 있습니다. SageMaker TensorFlow Serving 컨테이너를 사용하여 GPU 가속 인스턴스를 사용하여 수십만 개의 이미지에 대한 추론을 빠르게 얻는 방법을 확인하였습니다.

Amazon SageMaker TFS 컨테이너는 CSV 및 JSON 데이터를 바로 지원합니다. 컨테이너의 전처리 및 후처리 스크립트 기능을 사용하면 모든 형식의 데이터에 대해 변환 작업을 실행할 수 있습니다. Amazon SageMaker 호스팅 모델 엔드포인트를 사용하여 실시간 추론에도 동일한 컨테이너를 사용할 수 있습니다.